In [2]:
%pip install kaggle

  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
  Preparing metadata (pyproject.toml): started
  Preparing metadata (pyproject.toml): finished with status 'done'
  Using cached bleach-6.2.0-py3-none-any.whl.metadata (30 kB)
  Using cached webencodings-0.5.1-py2.py3-none-any.whl.metadata (2.1 kB)
Using cached bleach-6.2.0-py3-none-any.whl (163 kB)
Using cached webencodings-0.5.1-py2.py3-none-any.whl (11 kB)
  Created wheel for kaggle: filename=kaggle-1.6.17-py3-none-any.whl size=105854 sha256=f330f571f1b06d030091f5dc221413d9a047d3941022d0dd9bc05cfda40c9b2c
  Stored in directory: c:\users\casper\appdata\local\pip\cache\wheels\ff\55\fb\b27a466be754d2a06ffe0e37b248d844f090a63b51becea85d
Successfully built kaggle
Note: you may need to restart the kernel to use updated packages.


DEPRECATION: Loading egg at c:\users\casper\appdata\local\programs\python\python311\lib\site-packages\vboxapi-1.0-py3.11.egg is deprecated. pip 25.1 will enforce this behaviour change. A possible replacement is to use pip for package installation. Discussion can be found at https://github.com/pypa/pip/issues/12330
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.
  Consider adding this directory to PATH or, if you prefer to suppress this warning, use --no-warn-script-location.

[notice] A new release of pip is available: 25.0 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [11]:
import os
import json
from kaggle.api.kaggle_api_extended import KaggleApi

# Kaggle kimlik bilgileri
kaggle_credentials = {
    "username": "serafettindoruksezer",
    "key": "a17adbda3bbfa8a08f8f23919c7b01bf"
}

# Geçici olarak `kaggle.json` dosyasını oluşturma
kaggle_dir = os.path.expanduser("~/.kaggle")
os.makedirs(kaggle_dir, exist_ok=True)
kaggle_json_path = os.path.join(kaggle_dir, "kaggle.json")

with open(kaggle_json_path, "w") as f:
    json.dump(kaggle_credentials, f)

os.chmod(kaggle_json_path, 0o600)  # Dosya izinlerini ayarla

# Kaggle API doğrulama
def test_kaggle_api():
    try:
        api = KaggleApi()
        api.authenticate()
        print("Kaggle API başarıyla doğrulandı!")
        return api
    except Exception as e:
        print(f"Kaggle API doğrulama hatası: {e}")
        return None

# API'yi doğrulama ve kullanma
api = test_kaggle_api()

if api:
    # Örnek: Kaggle'dan veri seti listesi alma
    datasets = api.datasets_list()
    print("Kaggle üzerindeki veri setlerinden bazıları:")
    for dataset in datasets[:5]:  # İlk 5 veri setini yazdır
        print(f"{dataset['ref']}: {dataset['title']}")


Kaggle API başarıyla doğrulandı!
Kaggle üzerindeki veri setlerinden bazıları:
asinow/car-price-dataset: Car Price Dataset
adilshamim8/sleep-cycle-and-productivity: Sleep Cycle & Productivity
akxiit/blinkit-sales-dataset: Blinkit Sales Dataset
adilshamim8/education-and-career-success: Education & Career Success.
asinow/schizohealth-dataset: Schizophrenia Dataset


In [13]:
import os
import json
import zipfile
import pandas as pd
from kaggle.api.kaggle_api_extended import KaggleApi

# Kaggle kimlik bilgileri
kaggle_credentials = {
    "username": "serafettindoruksezer",  # Kaggle kullanıcı adınız
    "key": "a17adbda3bbfa8a08f8f23919c7b01bf"  # Kaggle API anahtarınız
}

# Geçici olarak `kaggle.json` dosyasını oluşturma
kaggle_dir = os.path.expanduser("~/.kaggle")
os.makedirs(kaggle_dir, exist_ok=True)
kaggle_json_path = os.path.join(kaggle_dir, "kaggle.json")

with open(kaggle_json_path, "w") as f:
    json.dump(kaggle_credentials, f)

os.chmod(kaggle_json_path, 0o600)  # Dosya izinlerini ayarla

# Kaggle API doğrulama
def authenticate_kaggle_api():
    try:
        api = KaggleApi()
        api.authenticate()
        print("Kaggle API başarıyla doğrulandı!")
        return api
    except Exception as e:
        print(f"Kaggle API doğrulama hatası: {e}")
        return None

# Kaggle API ile veri setlerini indirme
def download_dataset(api, dataset_slug, download_path):
    try:
        api.dataset_download_files(dataset_slug, path=download_path, unzip=True)
        print(f"{dataset_slug} başarıyla indirildi ve açıldı: {download_path}")
    except Exception as e:
        print(f"{dataset_slug} indirilirken hata oluştu: {e}")

# Veri setindeki trafik ışıkları ve hız sınırı levhalarını analiz etme
def analyze_dataset(dataset_path):
    # Varsayılan değerler
    total_traffic_lights = 0
    speed_limit_counts = {10: 0, 20: 0, 30: 0, 40: 0, 50: 0, 60: 0, 70: 0, 80: 0, 90: 0, 100: 0, 110: 0, 120: 0}
    class_count = 0
    roboflow_used = "Belirsiz"
    environment = "CARLA Simülatörü"
    notes = ""

    # Etiket dosyasını analiz et (JSON, CSV vb. formatlar)
    for root, dirs, files in os.walk(dataset_path):
        for file in files:
            if file.endswith('.json') or file.endswith('.csv') or file.endswith('.txt'):
                label_file_path = os.path.join(root, file)
                try:
                    if file.endswith('.json'):
                        import json
                        with open(label_file_path, 'r') as f:
                            data = json.load(f)

                        #Örnek json okuma
                        if 'annotations' in data:
                            for annotation in data['annotations']:
                                if 'category_id' in annotation:
                                    category_id = annotation['category_id']
                                    if category_id == 1:
                                        total_traffic_lights += 1
                                    elif 10 <= category_id <= 21: # Varsayılan category idler (deneyerek doğrulayın)
                                        speed_limit = (category_id - 1) * 10 # 10,20...120 gibi.
                                        speed_limit_counts[speed_limit] = speed_limit_counts.get(speed_limit, 0) +1



                    elif file.endswith('.csv'):
                        df = pd.read_csv(label_file_path)
                        # CSV'deki sınıf bilgilerini analiz edin
                        # **Buraya veri setine özel CSV analiz kodunuzu ekleyin**

                        #Örnek csv okuma

                        for column in df.columns:

                         if "traffic_light" in column:
                            total_traffic_lights=len(df[column].unique())  # varsayılan değer
                         if "speed_limit" in column:
                              for speed in range(10,130,10):
                               speed_limit_counts[speed]= len(df[df[column] == speed])


                    elif file.endswith('.txt'):
                        with open(label_file_path, 'r') as f:
                            lines = f.readlines()
                        # TXT dosyasındaki sınıf bilgilerini analiz edin
                        # **Buraya veri setine özel TXT analiz kodunuzu ekleyin**

                        # Örnek txt okuma (satır satır okuyarak)

                        for line in lines:

                             if "traffic_light" in line:
                               total_traffic_lights += 1  #satırda bu bilgi geçiyorsa
                             if "speed_limit" in line:

                                 try:
                                   speed=int(line.split("speed_limit:")[-1])  # sayıyı ayır.
                                   if 10<=speed<=120 and speed%10 ==0:   #sağlama
                                        speed_limit_counts[speed]=speed_limit_counts.get(speed, 0)+1
                                 except:
                                        print("Geçersiz speed verisi.")


                except Exception as e:
                    notes += f"Error analyzing file {file}: {str(e)}\n"

    # class_count güncellenmesi: trafik ışığı + hız limitleri
    class_count = 1  # Trafik ışığı
    for speed in speed_limit_counts:
        if speed_limit_counts[speed] > 0:  # Sadece kullanılan hız limitlerini say
            class_count += 1

    return total_traffic_lights, speed_limit_counts, class_count, roboflow_used, environment, notes

# Excel dosyası oluşturma
def create_excel(datasets, output_file, api):
    data = []

    for dataset_name, dataset_link, dataset_slug in datasets:
        # Veri setini indir
        dataset_path = f"datasets/{dataset_name.replace(' ', '_')}"
        os.makedirs(dataset_path, exist_ok=True)
        download_dataset(api, dataset_slug, dataset_path)

        # Veri setini analiz et
        total_traffic_lights, speed_limit_counts, class_count, roboflow_used, environment, notes = analyze_dataset(dataset_path)

        # Excel için bir satır oluştur
        row = {
            "Dataset Adı": dataset_name,
            "Dataset Linki": dataset_link,
            "Toplam Trafik Işığı Sayısı": total_traffic_lights,
            "10 Hız Levhası": speed_limit_counts.get(10,0),
            "20 Hız Levhası": speed_limit_counts.get(20,0),
            "30 Hız Levhası": speed_limit_counts.get(30,0),
            "40 Hız Levhası": speed_limit_counts.get(40,0),
            "50 Hız Levhası": speed_limit_counts.get(50,0),
            "60 Hız Levhası": speed_limit_counts.get(60,0),
            "70 Hız Levhası": speed_limit_counts.get(70,0),
            "80 Hız Levhası": speed_limit_counts.get(80,0),
            "90 Hız Levhası": speed_limit_counts.get(90,0),
            "100 Hız Levhası": speed_limit_counts.get(100,0),
            "110 Hız Levhası": speed_limit_counts.get(110,0),
            "120 Hız Levhası": speed_limit_counts.get(120,0),
            "Kullanılan Sınıf Sayısı": class_count,
            "Roboflow Kullanımı (Evet/Hayır/Belirsiz)": roboflow_used,
            "Ortam": environment,
            "Açıklamalar/Ek Notlar": notes
        }
        data.append(row)

    # DataFrame'i Excel dosyasına yaz
    df = pd.DataFrame(data)
    df.to_excel(output_file, index=False)

# Kaggle veri setleri bilgileri
datasets = [
    ("CARLA Object Detection Dataset", "https://www.kaggle.com/datasets/suraj520/carla-object-detection-dataset/data", "suraj520/carla-object-detection-dataset"),
    ("CARLA Dataset", "https://www.kaggle.com/datasets/alechantson/carladataset", "alechantson/carladataset"),
    ("Object Detection CARLA Self-Driving Car", "https://www.kaggle.com/datasets/ibrahimalobaid/object-detection-carla-self-driving-car?select=README.dataset.txt", "ibrahimalobaid/object-detection-carla-self-driving-car"),
    ("CARLA Traffic Signs Images", "https://www.kaggle.com/datasets/sachsene/carla-traffic-signs-images", "sachsene/carla-traffic-signs-images"),
    ("CARLA Traffic Lights Images", "https://www.kaggle.com/datasets/sachsene/carla-traffic-lights-images", "sachsene/carla-traffic-lights-images")
]

# API'yi doğrula
api = authenticate_kaggle_api()

if api:
    # Excel dosyasını oluştur
    output_file = "CARLA_Dataset_Analysis.xlsx"
    create_excel(datasets, output_file, api)
    print(f"Excel dosyası oluşturuldu: {output_file}")
else:
    print("API doğrulama hatası nedeniyle Excel dosyası oluşturulamadı.")

Kaggle API başarıyla doğrulandı!
Dataset URL: https://www.kaggle.com/datasets/suraj520/carla-object-detection-dataset
suraj520/carla-object-detection-dataset başarıyla indirildi ve açıldı: datasets/CARLA_Object_Detection_Dataset
Dataset URL: https://www.kaggle.com/datasets/alechantson/carladataset
alechantson/carladataset başarıyla indirildi ve açıldı: datasets/CARLA_Dataset
Dataset URL: https://www.kaggle.com/datasets/ibrahimalobaid/object-detection-carla-self-driving-car
ibrahimalobaid/object-detection-carla-self-driving-car başarıyla indirildi ve açıldı: datasets/Object_Detection_CARLA_Self-Driving_Car
Dataset URL: https://www.kaggle.com/datasets/sachsene/carla-traffic-signs-images
sachsene/carla-traffic-signs-images başarıyla indirildi ve açıldı: datasets/CARLA_Traffic_Signs_Images
Dataset URL: https://www.kaggle.com/datasets/sachsene/carla-traffic-lights-images
sachsene/carla-traffic-lights-images başarıyla indirildi ve açıldı: datasets/CARLA_Traffic_Lights_Images
Excel dosyası ol

In [4]:
import os
import pandas as pd

# Resimlerin bulunduğu klasörde analiz yapma
def analyze_images(image_folder):
    # Trafik ışıkları ve hız levhaları için varsayılan sayılar
    total_traffic_lights = 0
    speed_limit_counts = {10: 0, 20: 0, 30: 0, 40: 0, 50: 0, 60: 0, 70: 0, 80: 0, 90: 0, 100: 0, 110: 0, 120: 0}

    # Klasördeki resimleri tarama
    for root, dirs, files in os.walk(image_folder):
        for file in files:
            # Dosya adı kontrolü (örneğin, trafik ışığı ve hız levhası bilgisi dosya adında belirtilmiş olabilir)
            file_lower = file.lower()
            if "traffic_light" in file_lower:
                total_traffic_lights += 1
            for speed in speed_limit_counts.keys():
                if f"speed_limit_{speed}" in file_lower or f"speed_{speed}" in file_lower:
                    speed_limit_counts[speed] += 1

    return total_traffic_lights, speed_limit_counts

# Excel tablosu oluşturma
def create_excel(datasets, output_file):
    data = []

    for dataset in datasets:
        dataset_name = dataset.get("name")
        dataset_link = dataset.get("link")
        image_folder = dataset.get("path")
        roboflow_used = dataset.get("roboflow_used", "Belirsiz")
        environment = dataset.get("environment", "CARLA Simülatörü")
        notes = dataset.get("notes", "")

        # Resimleri analiz et
        total_traffic_lights, speed_limit_counts = analyze_images(image_folder)

        # Toplam sınıf sayısını hesapla (örneğin, trafik ışıkları + hız sınırı levhaları)
        class_count = sum(1 for count in speed_limit_counts.values() if count > 0) + (1 if total_traffic_lights > 0 else 0)

        # Excel için bir satır oluştur
        row = {
            "Dataset Adı": dataset_name,
            "Dataset Linki": dataset_link,
            "Toplam Trafik Işığı Sayısı": total_traffic_lights,
            "10 Hız Levhası": speed_limit_counts[10],
            "20 Hız Levhası": speed_limit_counts[20],
            "30 Hız Levhası": speed_limit_counts[30],
            "40 Hız Levhası": speed_limit_counts[40],
            "50 Hız Levhası": speed_limit_counts[50],
            "60 Hız Levhası": speed_limit_counts[60],
            "70 Hız Levhası": speed_limit_counts[70],
            "80 Hız Levhası": speed_limit_counts[80],
            "90 Hız Levhası": speed_limit_counts[90],
            "100 Hız Levhası": speed_limit_counts[100],
            "110 Hız Levhası": speed_limit_counts[110],
            "120 Hız Levhası": speed_limit_counts[120],
            "Kullanılan Sınıf Sayısı": class_count,
            "Roboflow Kullanımı (Evet/Hayır/Belirsiz)": roboflow_used,
            "Ortam": environment,
            "Açıklamalar/Ek Notlar": notes
        }
        data.append(row)

    # DataFrame'i Excel dosyasına yaz
    df = pd.DataFrame(data)
    df.to_excel(output_file, index=False)

# Veri seti bilgileri
datasets = [
    {
        "name": "CARLA Object Detection Dataset",
        "link": "https://www.kaggle.com/datasets/suraj520/carla-object-detection-dataset/data",
        "path": "datasets/carla_object_detection",
        "roboflow_used": "Hayır",
        "environment": "CARLA Simülatörü",
        "notes": "CARLA nesne tespiti veri seti."
    },
    {
        "name": "CARLA Dataset",
        "link": "https://www.kaggle.com/datasets/alechantson/carladataset",
        "path": "datasets/carla_dataset",
        "roboflow_used": "Hayır",
        "environment": "CARLA Simülatörü",
        "notes": "CARLA genel veri seti."
    },
    {
        "name": "Object Detection CARLA Self-Driving Car",
        "link": "https://www.kaggle.com/datasets/ibrahimalobaid/object-detection-carla-self-driving-car?select=README.dataset.txt",
        "path": "datasets/object_detection_carla",
        "roboflow_used": "Belirsiz",
        "environment": "CARLA Simülatörü",
        "notes": "Otonom sürüş veri seti."
    },
    {
        "name": "CARLA Traffic Signs Images",
        "link": "https://www.kaggle.com/datasets/sachsene/carla-traffic-signs-images",
        "path": "datasets/carla_traffic_signs",
        "roboflow_used": "Evet",
        "environment": "CARLA Simülatörü",
        "notes": "Trafik levhaları veri seti."
    },
    {
        "name": "CARLA Traffic Lights Images",
        "link": "https://www.kaggle.com/datasets/sachsene/carla-traffic-lights-images",
        "path": "datasets/carla_traffic_lights",
        "roboflow_used": "Hayır",
        "environment": "CARLA Simülatörü",
        "notes": "Trafik ışıkları veri seti."
    }
]

# Excel dosyasını oluştur
output_file = "CARLA_Dataset_Analysis.xlsx"
create_excel(datasets, output_file)
print(f"Excel dosyası oluşturuldu: {output_file}")


Excel dosyası oluşturuldu: CARLA_Dataset_Analysis.xlsx


In [2]:
import os
import cv2
import pandas as pd
from ultralytics import YOLO

# ✅ YOLOv5 modelini yükle (Önceden eğitilmiş model)
model = YOLO("yolov8n.pt")  # Daha iyi sonuç için "yolov8s.pt" veya özel bir model kullanabilirsin.

# ✅ Kullanılacak veri yolları
datasets = [
    {
        "name": "CARLA Object Detection Dataset",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\test",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\train"
        ]
    },
    {
        "name": "CARLA Dataset",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Dataset\CARLA-DATASET.v1-carla_v1.coco\train",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Dataset\CARLA-DATASET.v1-carla_v1.coco\valid",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Dataset\CARLA-DATASET.v1-carla_v1.yolov5pytorch\train\images",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Dataset\CARLA-DATASET.v1-carla_v1.yolov5pytorch\valid\images"
        ]
    },
    {
        "name": "Object Detection CARLA Self-Driving Car",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\Object_Detection_CARLA_Self-Driving_Car\train\images",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\Object_Detection_CARLA_Self-Driving_Car\valid\images"
        ]
    }
]

# ✅ Tespit edilecek sınıflar
target_classes = {
    "traffic_light": 0,
    "speed_limit_10": 1,
    "speed_limit_20": 2,
    "speed_limit_30": 3,
    "speed_limit_40": 4,
    "speed_limit_50": 5,
    "speed_limit_60": 6,
    "speed_limit_70": 7,
    "speed_limit_80": 8,
    "speed_limit_90": 9,
    "speed_limit_100": 10,
    "speed_limit_110": 11,
    "speed_limit_120": 12,
    "stop_sign": 13
}

# ✅ Sonuçları saklayacağımız liste
data = []

# ✅ Klasörleri tek tek gez ve tespit yap
for dataset in datasets:
    dataset_name = dataset["name"]
    total_counts = {label: 0 for label in target_classes.keys()}

    for folder in dataset["path"]:
        if not os.path.exists(folder):
            print(f"⚠️ Uyarı: {folder} klasörü bulunamadı!")
            continue

        for file in os.listdir(folder):
            if file.endswith((".jpg", ".png", ".jpeg")):
                image_path = os.path.join(folder, file)

                # 📌 YOLO modelini çalıştır
                results = model(image_path)

                # 📌 Sonuçları işle
                for result in results:
                    for box in result.boxes:
                        class_id = int(box.cls[0].item())

                        # 📌 Eğer sınıf tanımlıysa, sayıyı artır
                        for label, target_id in target_classes.items():
                            if class_id == target_id:
                                total_counts[label] += 1

    # ✅ Excel için satır oluştur
    row = {
        "Dataset Adı": dataset_name,
        "Toplam Trafik Işığı": total_counts["traffic_light"],
        "10 Hız Levhası": total_counts["speed_limit_10"],
        "20 Hız Levhası": total_counts["speed_limit_20"],
        "30 Hız Levhası": total_counts["speed_limit_30"],
        "40 Hız Levhası": total_counts["speed_limit_40"],
        "50 Hız Levhası": total_counts["speed_limit_50"],
        "60 Hız Levhası": total_counts["speed_limit_60"],
        "70 Hız Levhası": total_counts["speed_limit_70"],
        "80 Hız Levhası": total_counts["speed_limit_80"],
        "90 Hız Levhası": total_counts["speed_limit_90"],
        "100 Hız Levhası": total_counts["speed_limit_100"],
        "110 Hız Levhası": total_counts["speed_limit_110"],
        "120 Hız Levhası": total_counts["speed_limit_120"],
        "Stop Levhası": total_counts["stop_sign"]
    }
    data.append(row)

# ✅ Excel'e kaydet
df = pd.DataFrame(data)
excel_path = "CARLA_Dataset_Analysis.xlsx"
df.to_excel(excel_path, index=False)

print(f"🎯 İşlem tamamlandı! Sonuçlar '{excel_path}' dosyasına kaydedildi.")



image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\test\Town05_001920.png: 384x640 1 person, 80.5ms
Speed: 2.0ms preprocess, 80.5ms inference, 2.0ms postprocess per image at shape (1, 3, 384, 640)

image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\test\Town05_001980.png: 384x640 1 car, 67.2ms
Speed: 2.0ms preprocess, 67.2ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\test\Town05_002040.png: 384x640 2 cars, 68.5ms
Speed: 1.0ms preprocess, 68.5ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traf

### Trafik ışığı diğer kısım.

In [ ]:
import os
import pandas as pd
from ultralytics import YOLO

# ✅ YOLOv5 modelini yükle
model = YOLO("yolov8n.pt")  # Daha iyi sonuç için "yolov8s.pt" veya özel bir model kullanabilirsin.

# ✅ Kullanılacak yeni veri yolları
datasets = [
    {
        "name": "CARLA Traffic Lights Images",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\train\green",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\train\red",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\train\yellow",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\val\green",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\val\red",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\val\yellow"
        ]
    },
    {
        "name": "CARLA Traffic Signs Images",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_30",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_60",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_90",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_limit_30",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_limit_40",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_limit_60",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\stop",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\val\speed_30",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\val\speed_60",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\val\speed_90",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\val\speed_limit_30",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\val\speed_limit_40",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\val\speed_limit_60",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\val\stop"
        ]
    }
]

# ✅ Tespit edilecek sınıflar
target_classes = {
    "traffic_light": 0,
    "speed_limit_30": 1,
    "speed_limit_40": 2,
    "speed_limit_60": 3,
    "speed_limit_90": 4,
    "stop_sign": 5
}

# ✅ Sonuçları saklayacağımız liste
data = []

# ✅ Klasörleri tek tek gez ve tespit yap
for dataset in datasets:
    dataset_name = dataset["name"]
    total_counts = {label: 0 for label in target_classes.keys()}

    for folder in dataset["path"]:
        if not os.path.exists(folder):
            print(f"⚠️ Uyarı: {folder} klasörü bulunamadı!")
            continue

        for file in os.listdir(folder):
            if file.endswith((".jpg", ".png", ".jpeg")):
                image_path = os.path.join(folder, file)

                # 📌 YOLO modelini çalıştır
                results = model(image_path)

                # 📌 Sonuçları işle
                for result in results:
                    for box in result.boxes:
                        class_id = int(box.cls[0].item())

                        # 📌 Eğer sınıf tanımlıysa, sayıyı artır
                        for label, target_id in target_classes.items():
                            if class_id == target_id:
                                total_counts[label] += 1

    # ✅ Excel için satır oluştur
    row = {
        "Dataset Adı": dataset_name,
        "Toplam Trafik Işığı": total_counts["traffic_light"],
        "30 Hız Levhası": total_counts["speed_limit_30"],
        "40 Hız Levhası": total_counts["speed_limit_40"],
        "60 Hız Levhası": total_counts["speed_limit_60"],
        "90 Hız Levhası": total_counts["speed_limit_90"],
        "Stop Levhası": total_counts["stop_sign"]
    }
    data.append(row)

# ✅ Excel'e kaydet
df = pd.DataFrame(data)
excel_path = "CARLA_Traffic_Analysis.xlsx"
df.to_excel(excel_path, index=False)

print(f"🎯 İşlem tamamlandı! Sonuçlar '{excel_path}' dosyasına kaydedildi.")



image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\train\green\green_1.jpg: 640x384 (no detections), 92.0ms
Speed: 2.6ms preprocess, 92.0ms inference, 2.0ms postprocess per image at shape (1, 3, 640, 384)

image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\train\green\green_10.jpg: 640x384 (no detections), 58.0ms
Speed: 2.0ms preprocess, 58.0ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 384)

image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\train\green\green_100.jpg: 640x256 (no detections), 94.4ms
Speed: 2.0ms preprocess, 94.4ms inference, 0.0ms postprocess per image at shape (1, 3, 640, 256)

image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_

### TÜM KOD

In [1]:
import os
import pandas as pd
from ultralytics import YOLO

# ✅ YOLO modeli yükleniyor (Önceden eğitilmiş model)
model = YOLO("yolov8n.pt")  # Daha iyi sonuç için "yolov8s.pt" veya özel bir model kullanabilirsiniz.

# ✅ Tüm veri setlerini birleştirme
datasets = [
    {
        "name": "CARLA Object Detection Dataset",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\test",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\train"
        ]
    },
    {
        "name": "CARLA Dataset",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Dataset\CARLA-DATASET.v1-carla_v1.coco\train",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Dataset\CARLA-DATASET.v1-carla_v1.coco\valid",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Dataset\CARLA-DATASET.v1-carla_v1.yolov5pytorch\train\images",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Dataset\CARLA-DATASET.v1-carla_v1.yolov5pytorch\valid\images"
        ]
    },
    {
        "name": "Object Detection CARLA Self-Driving Car",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\Object_Detection_CARLA_Self-Driving_Car\train\images",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\Object_Detection_CARLA_Self-Driving_Car\valid\images"
        ]
    },
    {
        "name": "CARLA Traffic Lights Images",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\train\green",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\train\red",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\train\yellow",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\val\green",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\val\red",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Lights_Images\traffic_light_data\val\yellow"
        ]
    },
    {
        "name": "CARLA Traffic Signs Images",
        "path": [
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_10",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_20",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_30",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_40",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_50",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_60",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_70",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_80",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\speed_90",
            r"C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Traffic_Signs_Images\traffic_signs\train\stop"
        ]
    }
]

# ✅ Ortak tespit edilecek sınıflar
target_classes = {
    "traffic_light": 0,
    "speed_limit_10": 1,
    "speed_limit_20": 2,
    "speed_limit_30": 3,
    "speed_limit_40": 4,
    "speed_limit_50": 5,
    "speed_limit_60": 6,
    "speed_limit_70": 7,
    "speed_limit_80": 8,
    "speed_limit_90": 9,
    "speed_limit_100": 10,
    "speed_limit_110": 11,
    "speed_limit_120": 12,
    "stop_sign": 13
}

# ✅ Sonuçları saklamak için liste
data = []

# ✅ Her veri setini dolaşarak YOLO modelini çalıştır
for dataset in datasets:
    dataset_name = dataset["name"]
    total_counts = {label: 0 for label in target_classes.keys()}

    for folder in dataset["path"]:
        if not os.path.exists(folder):
            print(f"⚠️ Uyarı: {folder} klasörü bulunamadı!")
            continue

        for file in os.listdir(folder):
            if file.endswith((".jpg", ".png", ".jpeg")):
                image_path = os.path.join(folder, file)

                # 📌 YOLO modelini çalıştır
                results = model(image_path)

                # 📌 Sonuçları işle
                for result in results:
                    for box in result.boxes:
                        class_id = int(box.cls[0].item())

                        # 📌 Eğer sınıf tanımlıysa, sayıyı artır
                        for label, target_id in target_classes.items():
                            if class_id == target_id:
                                total_counts[label] += 1

    # ✅ Excel için satır oluştur
    row = {"Dataset Adı": dataset_name}
    row.update(total_counts)
    data.append(row)

# ✅ Excel'e kaydet
df = pd.DataFrame(data)
excel_path = "CARLA_Merged_Dataset_Analysis.xlsx"
df.to_excel(excel_path, index=False)

print(f"🎯 İşlem tamamlandı! Sonuçlar '{excel_path}' dosyasına kaydedildi.")



image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\test\Town05_001920.png: 384x640 1 person, 1354.0ms
Speed: 11.2ms preprocess, 1354.0ms inference, 24.6ms postprocess per image at shape (1, 3, 384, 640)

image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\test\Town05_001980.png: 384x640 1 car, 1199.8ms
Speed: 2.0ms preprocess, 1199.8ms inference, 4.6ms postprocess per image at shape (1, 3, 384, 640)

image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uygulama_Yolo_traffic_sign_detection\datasets\CARLA_Object_Detection_Dataset\carla-object-detection-dataset\images\test\Town05_002040.png: 384x640 2 cars, 1265.5ms
Speed: 29.2ms preprocess, 1265.5ms inference, 4.9ms postprocess per image at shape (1, 3, 384, 640)

image 1/1 C:\Users\Casper\Desktop\Bitirme_2_Rapor_Uyg